In [2]:
import numpy as np
import pandas as pd
import geopandas as gpd
import datetime as dt
import requests
import zipfile
import geodatasets
from astral import LocationInfo 
from astral.sun import sun
from astral.location import Location
from bs4 import BeautifulSoup
from scipy import stats
import redis
import json

#### connect to a Redis database

In [3]:
r = redis.Redis(host='localhost', port=6379, db=0)

### user input

In [15]:
year = 2024
month = 10
wojewodztwo = "mazowieckie"
powiat = "warszawski zachodni"
parameter = "temperature"

city = LocationInfo("Warsaw", "Poland", "Europe/Warsaw", 52.22977, 21.01178)
warsaw = Location(city)

#### station data
Effacility data attributes: 
- ifcid - kod stacji

In [8]:
effacility_path = r"dane_meteorologiczne\effacility.geojson"
effacility = gpd.read_file(effacility_path)

# print(effacility.head())

effacility = effacility.to_crs(epsg=2180)
effacility.plot(markersize=1, color="red")

<Axes: >

### administrative data
reads shapefiles of powiaty and województwa

In [ ]:
woj_path = r"dane_administracyjne\woj.shp"
powiaty_path = r"dane_administracyjne\powiaty.shp"

woj_data = gpd.read_file(woj_path)
woj = woj_data.to_crs(epsg=2180)
woj.plot()

powiaty_data = gpd.read_file(powiaty_path)
powiaty = powiaty_data.to_crs(epsg=2180)
powiaty.plot()

wojewodztwo_gpd = woj_data[woj_data["name"] == wojewodztwo]
powiat_gpd = powiaty_data[powiaty_data["name"] == powiat]


### download meteo data

In [ ]:
requests_path = "https://danepubliczne.imgw.pl/datastore/getfiledown/Arch/Telemetria/Meteo"

requests_path = requests_path + "/" + str(year) + "/Meteo_" + str(year) + "-" + str(month).zfill(2) + ".zip"
requests.get(requests_path)
if requests.get(requests_path).status_code == 200:
    data = requests.get(requests_path)
    with open("dane_meteorologiczne/Meteo.zip", "wb") as file:
        file.write(data.content)
    print("File downloaded")

# Unzip the file
with zipfile.ZipFile("dane_meteorologiczne/Meteo.zip", "r") as zip_ref:
    zip_ref.extractall("dane_meteorologiczne/Meteo")
    print("File unzipped")


#### read files to dataframes

Meteo data structure:
- 0 - kodSH stacji - station_code
- 1 - parametrSH - parameter_code
- 2 - data i godzina pomiaru - date
- 3 - wartość pomiaru - value


In [7]:
# Meteo files paths
air_temp_path = "dane_meteorologiczne/Meteo/B00300S_" + str(year) + "_" + str(month).zfill(2) + ".csv"
ground_temp_path = "dane_meteorologiczne/Meteo/B00305A_" + str(year) + "_" + str(month).zfill(2) + ".csv"
wind_direction_path = "dane_meteorologiczne/Meteo/B00202A_" + str(year) + "_" + str(month).zfill(2) + ".csv"
average_wind_speed_path = "dane_meteorologiczne/Meteo/B00702A_" + str(year) + "_" + str(month).zfill(2) + ".csv"
max_wind_speed_path = "dane_meteorologiczne/Meteo/B00703A_" + str(year) + "_" + str(month).zfill(2) + ".csv"
rainfall_10min_path = "dane_meteorologiczne/Meteo/B00608S_" + str(year) + "_" + str(month).zfill(2) + ".csv"
rainfall_24h_path = "dane_meteorologiczne/Meteo/B00604S_" + str(year) + "_" + str(month).zfill(2) + ".csv"
rainfall_1h_path = "dane_meteorologiczne/Meteo/B00606S_" + str(year) + "_" + str(month).zfill(2) + ".csv"
humidity_path = "dane_meteorologiczne/Meteo/B00802A_" + str(year) + "_" + str(month).zfill(2) + ".csv"
wind_gust_path = "dane_meteorologiczne/Meteo/B00714A_" + str(year) + "_" + str(month).zfill(2) + ".csv"
snow_water_reserve_path = "dane_meteorologiczne/Meteo/B00910A_" + str(year) + "_" + str(month).zfill(2) + ".csv"

all_paths = [air_temp_path, ground_temp_path, wind_direction_path, average_wind_speed_path, max_wind_speed_path, rainfall_10min_path, rainfall_24h_path, rainfall_1h_path, humidity_path, wind_gust_path, snow_water_reserve_path]
variables_names = ["air_temp", "ground_temp", "wind_direction", "average_wind_speed", "max_wind_speed", "rainfall_10min", "rainfall_24h", "rainfall_1h", "humidity", "wind_gust", "snow_water_reserve"]

dataframes = {}

for path in all_paths:
    # check if file exists
    try:
        data = pd.read_csv(path, delimiter=";", header=None, names=["station_code", "parameter_code", "date", "value"])
        dataframes[variables_names[all_paths.index(path)]] = data

        # change date to datetime format and set its as GMT timezone
        dataframes[variables_names[all_paths.index(path)]].date = pd.to_datetime(dataframes[variables_names[all_paths.index(path)]].date)
        dataframes[variables_names[all_paths.index(path)]].date = dataframes[variables_names[all_paths.index(path)]].date.dt.tz_localize("GMT")
                
    except FileNotFoundError:
        dataframes[variables_names[all_paths.index(path)]] = None
        print(f"Data not found: {path}, skipping...")

air_temp, ground_temp, wind_direction, average_wind_speed, max_wind_speed, rainfall_10min, rainfall_24h, rainfall_1h, humidity, wind_gust, snow_water_reserve = dataframes.values()

Data not found: dane_meteorologiczne/Meteo/B00910A_2024_10.csv, skipping...


stacja: {
    parametr: {
        rok_miesiac: {
            dzien1: {
                średnia ,
                średnia noc,
                mediana dzień,
                mediana noc,
                obcięta średnia dzień,
                obcięta średnia noc,
            },
            dzien2: {
                średnia dzień,
                średnia noc,
                mediana dzień,
                mediana noc,
                obcięta średnia dzień,
                obcięta średnia noc,
            }
            ...
        }
    }
}

### save parameters intor redis database

In [8]:
# chooose variable and station
try:
    if parameter == "temperature":
        dataframe = air_temp
    elif parameter == "ground_temperature":
        dataframe = ground_temp
    elif parameter == "wind_direction":
        dataframe = wind_direction
    elif parameter == "average_wind_speed":
        dataframe = average_wind_speed
    elif parameter == "max_wind_speed":
        dataframe = max_wind_speed
    elif parameter == "rainfall":
        dataframe = rainfall_10min
    elif parameter == "rainfall_24h":
        dataframe = rainfall_24h
    elif parameter == "rainfall_1h":
        dataframe = rainfall_1h
    elif parameter == "humidity":
        dataframe = humidity
    elif parameter == "wind_gust":
        dataframe = wind_gust
    elif parameter == "snow_water_reserve":
        dataframe = snow_water_reserve
except NameError:
    print("No data for this parameter")
    dataframe = None


In [18]:
days_in_month = dt.datetime(year, month+1, 1) - dt.datetime(year, month, 1)

stations = dataframe["station_code"].unique()

for station in stations:
    station_data = {}

    for day in range(1, days_in_month.days+1):
        date = dt.datetime(year, month, day)

        # Define that start and end of the day
        start = dt.datetime(year, month, day, 0, 0, 0)
        end = dt.datetime(year, month, day, 23, 59, 59)
        start = start.astimezone(dt.timezone.utc)
        end = end.astimezone(dt.timezone.utc)

        # Get sunrise and sunset times
        date = dt.datetime(year, month, day)
        sun_data = sun(city.observer, date=date.date(), tzinfo=city.timezone)
        sunrise = sun_data['sunrise']
        sunset = sun_data['sunset']

        # round times to nearest 10 minutes
        sunrise_rounded = sunrise.replace(minute=(10*round(sunrise.minute/10)) % 60)
        sunset_rounded = sunset.replace(minute=(10*round(sunset.minute/10)) % 60)
        sunset_rounded = sunset_rounded.replace(second=0, microsecond=0)
        sunrise_rounded = sunrise_rounded.replace(second=0, microsecond=0)

        # change to GMT time
        sunrise_rounded = sunrise_rounded.astimezone(dt.timezone.utc)
        sunset_rounded = sunset_rounded.astimezone(dt.timezone.utc)

        # extract data for the station and day
        this_station_data = dataframe[dataframe["station_code"] == station]
        this_station_data["date"] = pd.to_datetime(this_station_data["date"])

        # aggregate data for day and night
        day_data = this_station_data[(this_station_data["date"] >= sunrise_rounded) & (this_station_data["date"] <= sunset_rounded)]
        night_data = this_station_data[(this_station_data["date"] >= start) & (this_station_data["date"] <= end)]
        night_data = night_data[(night_data["date"] < sunrise_rounded) | (night_data["date"] > sunset_rounded)]

        mean_value_day = day_data["value"].mean()
        median_value_day = day_data["value"].median()
        trimmed_mean_value_day = stats.trim_mean(day_data["value"], 0.1)

        mean_value_night = night_data["value"].mean() 
        median_value_night = night_data["value"].median()
        trimmed_mean_value_night = stats.trim_mean(night_data["value"], 0.1)
        
        # save to a redis has with a name station_value_month
        day_key = f"{station}:{parameter}:{year}_{month}"
        if day_key not in station_data:
            station_data[day_key] = {}

        station_data[day_key][day] = {
            "day_average": mean_value_day,
            "night_average": mean_value_night,
            "day_median": median_value_day,
            "night_median": median_value_night,
            "day_trimmed_mean": trimmed_mean_value_day,
            "night_trimmed_mean": trimmed_mean_value_night,
        }

    for key, daily_data in station_data.items():
        for day, metrics in daily_data.items():
            redis_hash_key = f"{key}:{day}"

            # r.delete(redis_hash_key)
            if not r.exists(redis_hash_key):
                r.hset(redis_hash_key, mapping=metrics)


C:\Users\majak\AppData\Local\Temp\ipykernel_5860\3348552930.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  this_station_data["date"] = pd.to_datetime(this_station_data["date"])
C:\Users\majak\AppData\Local\Temp\ipykernel_5860\3348552930.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  this_station_data["date"] = pd.to_datetime(this_station_data["date"])
C:\Users\majak\AppData\Local\Temp\ipykernel_5860\3348552930.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from 